In [101]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import os
pd.set_option('display.float_format', lambda x: '%.3f' % x)

In [102]:
path_archivos = "./Data/"
os.listdir(path_archivos)

['MMM.csv', 'mmm.csv']

In [103]:
data_CF = pd.read_csv(path_archivos + 'MMM.csv')

In [104]:
medios = ['Print', 'Email', 'Radio', 'Facebook', 'Google', 'PayTV', 'OpenTV']
medios.sort()

## EDA

### Data Describe

El Dataset cuenta con 9 variables/features:

- 1: tiempo - Date 
- 2: inversion - Print 
- 4: inversion - Email
- 5: inversion - Radio      
- 6: inversion - Facebook    
- 7: inversion - Google      
- 8: inversion - PayTV       
- 9: inversion - OpenTV      
- 10: Ventas - Sales       

In [105]:
data_CF.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 200 entries, 0 to 199
Data columns (total 9 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   Date      200 non-null    object 
 1   OpenTV    200 non-null    float64
 2   PayTV     200 non-null    float64
 3   Radio     200 non-null    float64
 4   Print     200 non-null    float64
 5   Facebook  200 non-null    float64
 6   Google    200 non-null    float64
 7   Email     200 non-null    float64
 8   Sales     200 non-null    float64
dtypes: float64(8), object(1)
memory usage: 14.2+ KB


In [106]:
data_CF['Date'] = pd.to_datetime(data_CF['Date'])

In [107]:
data_CF['year_month'] = data_CF['Date'].dt.strftime('%Y-%m')

In [108]:
data_CF['InversionTotal'] = data_CF[medios].sum(axis=1)
data_CF['month'] = data_CF['Date'].dt.month
data_CF['year'] = data_CF['Date'].dt.year

In [109]:
#data_CF = data_CF.query('Date.dt.year == 2021')

### Descripcion de las distribuciones de inversion

- La mayor inversion se llevo acabo en OpenTV, con una inversion de 40,804.114
- La menor inversion se llevo acabo en Facebook, con una inversion de 317.35
- Google y Print  tienen una distribucion de inversiones muy similar 
- De igual manera la inversion en medios off como PayTV, Radio es parecida
- la inversion en Open TV y Facebook son muy similares

In [110]:
data_desc = data_CF[medios].describe().T
data_desc['cv'] = (data_desc['std'] / data_desc['mean']).round(3)
data_desc.sort_values(by='cv', ascending=False, inplace=True)
data_desc

count     mean      std   min     25%      50%       75%       max  \
PayTV    200.000 4270.423 5956.336 0.000   0.000    0.000 11486.889 16677.108   
OpenTV   200.000 5203.780 7015.914 0.000   0.000    0.000 13540.424 20376.516   
Radio    200.000 3117.853 4029.963 0.000   0.000    0.000  7703.643 10839.386   
Facebook 200.000 1888.857 2083.906 0.000   0.000    0.000  3989.989  5674.410   
Print    200.000 1260.607 1215.755 0.000   0.000 1424.187  2232.335  4551.527   
Google   200.000 4131.153 3881.221 0.000   0.000 5983.807  8013.008 10383.942   
Email    200.000 1829.250 1540.979 0.000 670.975 1409.492  3082.808  5658.230   

            cv  
PayTV    1.395  
OpenTV   1.348  
Radio    1.293  
Facebook 1.103  
Print    0.964  
Google   0.940  
Email    0.842

se puede observar que en promedio minimo se invierten por lo menos 1000 dolares

y OpenTV en promedio es quien mas invierte 8,257

In [111]:
count_actividad = pd.DataFrame()
for medio in medios:
    count_actividad[medio] = data_CF[medio].apply(lambda x: 1 if x > 0 else 0)
count_actividad = pd.melt(count_actividad,
                         value_vars=medios,
                         var_name='medios',
                         value_name='Semanas')
count_actividad = count_actividad.groupby(['medios'])['Semanas'].sum().reset_index()
px.bar(count_actividad,
      x='medios',
      y='Semanas',
      color='medios' ,
      text='Semanas',
      title='Numero de semanas que mantuvieron activa la inversion')

In [112]:
fig = make_subplots(rows=7, cols=1, subplot_titles=medios)
for i, medio in enumerate(medios):
    fig.add_trace(go.Scatter(x=data_CF['Date'], y=data_CF[medio], name=medio), row=i+1, col=1)
fig.update_layout(width=900, height=900)
fig.show()

podemos ver que print y email mantienen sus inversiones por mas numero de semanas 

mientras que los demas medios tienden a prender y apagar inversiones cada semana

In [113]:
def plot_histogram(medio):
    plot = px.histogram( data_CF[data_CF[medio] != 0],
                        x=medio,
                        marginal="box",
                        title="Histograma de " + medio)
    return plot

In [114]:
plot_histogram('PayTV')

PayTV realiza la mayor parte de inversion en torno a los 12,000 y 14,000

In [115]:
plot_histogram('OpenTV')

OpenTV realiza la mayor parte de inversion en torno a los 10,000 y 14,000 

In [116]:
plot_histogram('Facebook')

Facebook realiza la mayor parte de inversion en torno a los 4,000 y 5,000 

In [117]:
plot_histogram('Radio')

Radio realiza la mayor parte de inversion en torno a los 8,000 y 10,000

In [118]:
plot_histogram('Google')

Google realiza la mayor parte de inversion en torno a los 8,000 US y 6,000 US

In [119]:
plot_histogram('Print')

Print realiza la mayor parte de inversion en torno a los 2,000 US 

In [120]:
plot_histogram('Email')

Email realiza la mayor parte de inversion en torno a los 1,500 US 

In [121]:
data_CF_year_share = pd.DataFrame()
for medio in medios:
    data_CF_year_share[medio] =data_CF.groupby(['year'])[medios].sum().apply(lambda x: round((x[medio]*100) / x.sum(axis=0),3), axis=1)
data_CF_year_share = data_CF_year_share.reset_index()
data_CF_year_share = pd.melt(data_CF_year_share,
                            id_vars='year',
                            value_vars=medios,
                            var_name='medios',
                            value_name='% Participacion')
data_CF_year_share['year'] = data_CF_year_share['year'].astype(str)
plot_share = px.bar(data_CF_year_share,
              x = 'medios',
              y = '% Participacion',
              color='year',
              barmode='group',
              text='% Participacion')
#plot_share.update_traces(texttemplate='%{text:.0%}')
plot_share.show()

### Pie Chart

In [122]:
# creacion plot pie por año
fig = make_subplots(rows=1, 
                    cols=4, 
                    specs=[[{"type": "pie"}, {"type": "pie"}, {"type": "pie"}, {"type": "pie"}]], 
                    subplot_titles=[str(year) for year in data_CF['Date'].dt.year.unique()])
for i, year in enumerate(data_CF['Date'].dt.year.unique()):
    fig.add_trace(go.Pie(labels=medios, values=data_CF[data_CF['Date'].dt.year == year][medios].sum().values, name = str(year), hole=.5), row=1, col=i+1)
fig.update_layout( title_text="Inversion por año",
                    annotations=[dict(text='2018', x=0.107, y=0.46, font_size=18, showarrow=False),
                                dict(text='2019', x=0.370, y=0.46, font_size=18, showarrow=False),
                                dict(text='2020', x=0.631, y=0.46, font_size=18, showarrow=False),
                                dict(text='2021', x=0.895, y=0.46, font_size=18, showarrow=False)] )
fig.show()

En 2020 se decidio dar una mayor inversion a PayTV teniendo el segundo lugar en inversion y a Facebook tambien le dieron mas inversion su inversion 

In [123]:
data_pie = pd.melt(data_CF, 
                id_vars=['Date'], 
                value_vars=medios,
                var_name= "Medio",
                value_name= "Inversion")
pie_año = go.Figure(data=[go.Pie(labels=medios,
                                values=data_CF[medios].sum().values,
                                hole=0.5,
                                textinfo='label+percent')])
pie_año.update_layout(title_text='Share of Investment by Media')
pie_año

OpenTV es el principal medio de inversion 

In [124]:
com_mensual_medio = data_CF.groupby(['month'], as_index = False )[medios].sum()
com_mensual_medio = pd.melt(com_mensual_medio,
                           id_vars='month',
                           value_vars=medios,
                           var_name='medios',
                           value_name='inversion')
com_mensual_medio['month'] = com_mensual_medio['month'].astype(str)
px.bar(com_mensual_medio, 
       x= 'month', 
       y= 'inversion',
      color='medios'
      )

Diciembre es el mes con mayor inversion

In [125]:
data_CF.columns

Index(['Date', 'OpenTV', 'PayTV', 'Radio', 'Print', 'Facebook', 'Google',
       'Email', 'Sales', 'year_month', 'InversionTotal', 'month', 'year'],
      dtype='object')

In [126]:
fig = make_subplots(specs=[[{"secondary_y": True}]])

data_tem = data_CF.groupby(['year_month'], as_index = False )['InversionTotal', 'Sales'].sum()


fig.add_trace(go.Bar(x=data_tem['year_month'], 
                     y=data_tem['Sales'], 
                     marker_color='skyblue',
                     name='Sales'), secondary_y=False)

fig.add_trace(go.Scatter(x=data_tem['year_month'], 
                         y=data_tem['InversionTotal'],
                         marker_color='MediumPurple',
                         name='InversionTotal'), secondary_y=True)

fig.update_layout(  title='Inversion en medios vs Ventas', 
                    xaxis_title='year_month', 
                    yaxis_title='Inversion Total', 
                    barmode='group', 
#                    plot_bgcolor='white'
                )
fig.show()

/tmp/ipykernel_4761/936356401.py:3: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



se puede apreciar como las ventas responden positivamente a la inversion total de medios

In [127]:
px.line(data_CF.groupby(['month', 'year'])['InversionTotal'].sum().reset_index(), 
        x='month', 
        y='InversionTotal',
        color = 'year',
        title='investmen per year')


- Las inversiones de 2018 a 2020 se comportan de una manera muy similar
- La inversion en 2021 se ve que es notoriamente mas grande en cada mes
- noviembre normalmente baja la inversion para subir en diciembre

In [128]:
data_CF['InversionTotal'] = data_CF[medios].sum(axis=1)

In [129]:
import plotly.figure_factory as ff

df = data_CF[['Sales'] + medios].corr().round(2)

fig = ff.create_annotated_heatmap( df.values.tolist(),
                                    x=df.columns.values.tolist(),
                                    y=df.index.values.tolist(),
                                    colorscale='Viridis')
fig.update_layout(title_text='Correlacion')
fig['data'][0]['showscale'] = True
fig.show()

In [130]:
data_CF2 = data_CF.copy()

In [131]:
rho = 1
# 'Print', 'Email', 'Radio', 'Facebook', 'Google', 'PayTV', 'OpenTV'
medio = 'OpenTV'
data_CF2[medio+'_Adbug'] = data_CF2[medio]/(data_CF2[medio] + (data_CF2[medio].mean() * rho))

data_graf = data_CF2[[medio, medio+'_Adbug']]

px.scatter(x = data_graf[medio], 
           y = data_graf[medio+'_Adbug']
          )

## Creacion del Modelo

In [132]:
data_CF = data_CF.set_index('Date')
data_model = data_CF[medios+['Sales']]

In [133]:
from sklearn.model_selection import train_test_split

train, test = train_test_split(data_model, test_size=0.2, random_state=10)

distributions= np.array([len(train), len(test)])
print(distributions)

[160  40]


### Efecto de Saturacion

In [134]:
from scipy.signal import convolve2d
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.utils.validation import check_is_fitted, check_array

class ExponentialSaturation (BaseEstimator, TransformerMixin):
    def __init__ (self, a = 1.):
        self.a = a
        
    def fit(self, X, y = None):
        X = check_array(X) 
        self._check_n_features(X, reset = True)
        return self
    
    def transform (self, X):
        check_is_fitted (self)
        X = check_array (X)
        self._check_n_features (X, reset = False)
        
        # Adbudg
        #data_CF2.OpenTV/(data_CF2.OpenTV + (data_CF2.OpenTV.mean() * rho))
        # rho = self.a
        #return (X / (X + (X[X != 0].mean() * self.a)))
        return (X / (X + (X.mean() * self.a)))
        
        # exponencial
        #return 1 - np.exp (-self.a * X)

### Efecto de Arrastre

In [135]:
from sklearn.base import BaseEstimator, TransformerMixin

class ExponentialCarryover(BaseEstimator, TransformerMixin): 
    def __init__(self, strength = 0.5, length = 1):
        self.strength = strength
        self.length = length
        
    def fit(self, X, y = None):
        X = check_array(X)
        self._check_n_features(X, reset=True)
        self.sliding_window_ = (
            self.strength ** np.arange(self.length + 1)
        ).reshape(-1, 1)
        return self

    def transform(self, X: np.ndarray):
        check_is_fitted(self)
        X = check_array(X)
        self._check_n_features(X, reset=False)
        convolution = convolve2d(X, self.sliding_window_)
        if self.length > 0:
            convolution = convolution[: -self.length]
        return convolution

class ExponentialCarryover (BaseEstimator, TransformerMixin):
    def __init__ (self,  strength = 0.5, length = 1):
        self.strength = strength
        self.length = length
        
    def fit(self, X, y = None):
        X = check_array(X) 
        self._check_n_features(X, reset = True)
        return self
    
    def transform (self, X):
        check_is_fitted (self)
        X = check_array (X)
        self._check_n_features (X, reset = False)
        
        X_ = []
        val_ = 0
        contador = 0
        for val in X:
            if val != 0:
                contador = 0
            val = val + val_
            val_ = val * self.strength
            contador += 1
            if contador > self.length or val == 0:
                val_ = 0
                contador = 0
            X_.append(val)
        
        return np.array(X_)
        

### Pipeline

In [136]:
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.linear_model import LinearRegression, Ridge, ElasticNet
from sklearn.preprocessing import StandardScaler, MinMaxScaler

In [137]:

adstock = ColumnTransformer([
        ('OpenTV_pipe', Pipeline([
            ('carryover', ExponentialCarryover()),
            ('saturation', ExponentialSaturation())
        ]), ['OpenTV']),
        ('PayTV_pipe', Pipeline([
            ('carryover', ExponentialCarryover()),
            ('saturation', ExponentialSaturation())
        ]), ['PayTV']),
        ('Radio_pipe', Pipeline([
            ('carryover', ExponentialCarryover()),
            ('saturation', ExponentialSaturation())
        ]), ['Radio']),
        ('Print_pipe', Pipeline([
            ('carryover', ExponentialCarryover()),
            ('saturation', ExponentialSaturation())
        ]), ['Print']),
        ('Facebook_pipe', Pipeline([
            ('carryover', ExponentialCarryover()),
            ('saturation', ExponentialSaturation())
        ]), ['Facebook']),
        ('Google_pipe', Pipeline([
            ('carryover', ExponentialCarryover()),
            ('saturation', ExponentialSaturation())
        ]), ['Google']),
        ('Email_pipe', Pipeline([
            ('carryover', ExponentialCarryover()),
            ('saturation', ExponentialSaturation())
        ]), ['Email']),
])

model = Pipeline([
    ('adstock', adstock),
#    ('stdscaler', MinMaxScaler()),
    ('regression', LinearRegression())
])

### Diagrama de nuestro PipeLine

In [138]:
from sklearn import set_config

set_config(display="diagram")
model

Pipeline(steps=[('adstock',
                 ColumnTransformer(transformers=[('OpenTV_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['OpenTV']),
                                                 ('PayTV_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['PayTV']),
                                                 ('Radio_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   Exponent...
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['Facebook']),
                                                 ('Google_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['Google']),
                                                 ('Email_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['Email'])])),
                ('regression', LinearRegression())])

In [139]:
X_train = train.drop(columns='Sales')
Y_train = train['Sales']

In [140]:
X_train.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 160 entries, 2021-08-29 to 2018-03-11
Data columns (total 7 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   Email     160 non-null    float64
 1   Facebook  160 non-null    float64
 2   Google    160 non-null    float64
 3   OpenTV    160 non-null    float64
 4   PayTV     160 non-null    float64
 5   Print     160 non-null    float64
 6   Radio     160 non-null    float64
dtypes: float64(7)
memory usage: 10.0 KB


In [141]:
model.fit(X_train,Y_train)

Pipeline(steps=[('adstock',
                 ColumnTransformer(transformers=[('OpenTV_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['OpenTV']),
                                                 ('PayTV_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['PayTV']),
                                                 ('Radio_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   Exponent...
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['Facebook']),
                                                 ('Google_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['Google']),
                                                 ('Email_pipe',
                                                  Pipeline(steps=[('carryover',
                                                                   ExponentialCarryover()),
                                                                  ('saturation',
                                                                   ExponentialSaturation())]),
                                                  ['Email'])])),
                ('regression', LinearRegression())])

In [142]:
from sklearn.model_selection import cross_val_score, TimeSeriesSplit

x = data_model.drop(columns='Sales')
y = data_model['Sales']

print(cross_val_score(model, x, y, cv=TimeSeriesSplit()).mean())

0.4632199939999312


In [143]:
print(x.columns)
print('Coeficientes :', model[1].coef_)
print('Intersección :', model[1].intercept_)

Index(['Email', 'Facebook', 'Google', 'OpenTV', 'PayTV', 'Print', 'Radio'], dtype='object')
Coeficientes : [ 59867.06473189  32819.11989415  -8014.58535116  15800.57555897
 -13409.73693299  18896.49761824 144368.50298933]
Intersección : 108468.71877745495


In [144]:
def calculate_vif(X, used_cols):
    VIF = []
    for col in used_cols:
        cols = used_cols.copy()
        cols.remove(col)
        model = LinearRegression().fit(X[cols], X[col])
        VIF.append(1 / (1 - model.score(X[cols], X[col])))
    
    return VIF

In [145]:
x.columns

Index(['Email', 'Facebook', 'Google', 'OpenTV', 'PayTV', 'Print', 'Radio'], dtype='object')

In [146]:
used_cols = list(x.columns)
VIF = calculate_vif(x, used_cols)

In [147]:
VIF

[3.624688340796871,
 1.6545904166061325,
 3.2010076678797788,
 2.382115731988755,
 1.2167755695264588,
 1.5178738120512383,
 2.9996722069271278]

In [148]:
# Optuna nos ayuda a encontrar los mejores parametros
from optuna.integration import OptunaSearchCV
from optuna.distributions import UniformDistribution, IntUniformDistribution, CategoricalDistribution

- Para medios offline se prueba con distribuciones mas grandes de maximo 6 semanas de efecto de arrastre
- Para medion online se prueba con distribuciones mas pequeñas con un maximo de 3 semanas de efecto de arrastre

In [149]:
tuned_model = OptunaSearchCV(
    estimator=model,
    param_distributions={
        
        'adstock__OpenTV_pipe__carryover__strength':UniformDistribution(0.1, 1),  #Probara con valores de 0, 1
        'adstock__OpenTV_pipe__carryover__length':IntUniformDistribution(0, 6), #Probara con valores de 0, 6
        'adstock__OpenTV_pipe__saturation__a': UniformDistribution(0.1,1),     #Probara con valores de 0, 1
        
        'adstock__PayTV_pipe__carryover__strength':UniformDistribution(0.1, 1),
        'adstock__PayTV_pipe__carryover__length':IntUniformDistribution(0, 6),
        'adstock__PayTV_pipe__saturation__a': UniformDistribution(0.1,1),
        
        'adstock__Radio_pipe__carryover__strength':UniformDistribution(0.1, 1),
        'adstock__Radio_pipe__carryover__length':IntUniformDistribution(0, 6),
        'adstock__Radio_pipe__saturation__a':UniformDistribution(0.1, 1),
        
        'adstock__Print_pipe__carryover__strength':UniformDistribution(0.1, 1),
        'adstock__Print_pipe__carryover__length':IntUniformDistribution(0, 6),
        'adstock__Print_pipe__saturation__a':UniformDistribution(0.1, 1),
        
        'adstock__Facebook_pipe__carryover__strength':UniformDistribution(0.1, 1),
        'adstock__Facebook_pipe__carryover__length':IntUniformDistribution(0, 3),
        'adstock__Facebook_pipe__saturation__a':UniformDistribution(0.1, 1),
        
        'adstock__Google_pipe__carryover__strength':UniformDistribution(0.1, 1),
        'adstock__Google_pipe__carryover__length':IntUniformDistribution(0, 3),
        'adstock__Google_pipe__saturation__a':UniformDistribution(0.1, 1),
        
        'adstock__Email_pipe__carryover__strength':UniformDistribution(0.1, 1),
        'adstock__Email_pipe__carryover__length':IntUniformDistribution(0, 6),
        'adstock__Email_pipe__saturation__a':UniformDistribution(0.1, 1),
        
#        'regression__alpha':CategoricalDistribution([0.0001, 0.001,0.01,1]),
#        'regression__l1_ratio':CategoricalDistribution([0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1]),
#        'regression__fit_intercept':CategoricalDistribution([True,False]),
#        'regression__positive':CategoricalDistribution([True,False]),
#        'regression__selection':CategoricalDistribution(['cyclic', 'random']),
        
    },
    n_trials=1000,
    cv=TimeSeriesSplit(),
    random_state=0
)

/tmp/ipykernel_4761/191119638.py:1: ExperimentalWarning:

OptunaSearchCV is experimental (supported from v0.17.0). The interface can change in the future.



In [150]:
cross_val_score(tuned_model, x, y, cv = TimeSeriesSplit ()).mean()


/home/dsandovalflavio/anaconda3/envs/ProjectMMM/lib/python3.10/site-packages/sklearn/base.py:82: ExperimentalWarning:

OptunaSearchCV is experimental (supported from v0.17.0). The interface can change in the future.

[I 2022-04-12 14:11:43,998] A new study created in memory with name: no-name-799e39b1-33df-4910-aee7-e2b845fdb5b9
[I 2022-04-12 14:11:44,309] Trial 0 finished with value: -0.9866473942333969 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.5374425907193954, 'adstock__OpenTV_pipe__carryover__length': 4, 'adstock__OpenTV_pipe__saturation__a': 0.9870184455954389, 'adstock__PayTV_pipe__carryover__strength': 0.2760367691460003, 'adstock__PayTV_pipe__carryover__length': 4, 'adstock__PayTV_pipe__saturation__a': 0.9825239593893744, 'adstock__Radio_pipe__carryover__strength': 0.2624322676509575, 'adstock__Radio_pipe__carryover__length': 4, 'adstock__Radio_pipe__saturation__a': 0.8616785910698014, 'adstock__Print_pipe__carryover__strength': 0.8170383657279878, 'adstoc

[I 2022-04-12 14:11:45,858] Trial 6 finished with value: -2.8506446035295228 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.4661558975461523, 'adstock__OpenTV_pipe__carryover__length': 1, 'adstock__OpenTV_pipe__saturation__a': 0.734749816311523, 'adstock__PayTV_pipe__carryover__strength': 0.5268612674418802, 'adstock__PayTV_pipe__carryover__length': 1, 'adstock__PayTV_pipe__saturation__a': 0.33786660145125896, 'adstock__Radio_pipe__carryover__strength': 0.583889476305435, 'adstock__Radio_pipe__carryover__length': 5, 'adstock__Radio_pipe__saturation__a': 0.5925605493027641, 'adstock__Print_pipe__carryover__strength': 0.8250213947674001, 'adstock__Print_pipe__carryover__length': 2, 'adstock__Print_pipe__saturation__a': 0.1838075195059986, 'adstock__Facebook_pipe__carryover__strength': 0.6113585105606281, 'adstock__Facebook_pipe__carryover__length': 0, 'adstock__Facebook_pipe__saturation__a': 0.4696920768296541, 'adstock__Google_pipe__carryover__strength': 0.4962472237347

[I 2022-04-12 14:11:48,064] Trial 13 finished with value: -1.9160582057362254 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.34514567424173365, 'adstock__OpenTV_pipe__carryover__length': 6, 'adstock__OpenTV_pipe__saturation__a': 0.9933901441456867, 'adstock__PayTV_pipe__carryover__strength': 0.3354772002773254, 'adstock__PayTV_pipe__carryover__length': 4, 'adstock__PayTV_pipe__saturation__a': 0.7575784739001961, 'adstock__Radio_pipe__carryover__strength': 0.29797259157975087, 'adstock__Radio_pipe__carryover__length': 2, 'adstock__Radio_pipe__saturation__a': 0.8054502986712573, 'adstock__Print_pipe__carryover__strength': 0.6932735216841676, 'adstock__Print_pipe__carryover__length': 2, 'adstock__Print_pipe__saturation__a': 0.6768545800693364, 'adstock__Facebook_pipe__carryover__strength': 0.26095051664596614, 'adstock__Facebook_pipe__carryover__length': 1, 'adstock__Facebook_pipe__saturation__a': 0.2978151165713403, 'adstock__Google_pipe__carryover__strength': 0.27177926

[I 2022-04-12 14:11:50,532] Trial 20 finished with value: -0.8702395861129109 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.4393889344513455, 'adstock__OpenTV_pipe__carryover__length': 5, 'adstock__OpenTV_pipe__saturation__a': 0.439896183780773, 'adstock__PayTV_pipe__carryover__strength': 0.6154453230605297, 'adstock__PayTV_pipe__carryover__length': 0, 'adstock__PayTV_pipe__saturation__a': 0.14885044768786476, 'adstock__Radio_pipe__carryover__strength': 0.38824298679647573, 'adstock__Radio_pipe__carryover__length': 1, 'adstock__Radio_pipe__saturation__a': 0.5219506725640362, 'adstock__Print_pipe__carryover__strength': 0.1105154901337958, 'adstock__Print_pipe__carryover__length': 0, 'adstock__Print_pipe__saturation__a': 0.34846642496796126, 'adstock__Facebook_pipe__carryover__strength': 0.46476198586769646, 'adstock__Facebook_pipe__carryover__length': 0, 'adstock__Facebook_pipe__saturation__a': 0.5836306536124842, 'adstock__Google_pipe__carryover__strength': 0.40397062

[I 2022-04-12 14:11:52,868] Trial 27 finished with value: -0.44368022852532973 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.2101323369990934, 'adstock__OpenTV_pipe__carryover__length': 4, 'adstock__OpenTV_pipe__saturation__a': 0.5040045586830286, 'adstock__PayTV_pipe__carryover__strength': 0.7989341786381332, 'adstock__PayTV_pipe__carryover__length': 0, 'adstock__PayTV_pipe__saturation__a': 0.21714530271182247, 'adstock__Radio_pipe__carryover__strength': 0.6713670479598768, 'adstock__Radio_pipe__carryover__length': 0, 'adstock__Radio_pipe__saturation__a': 0.30994889170119283, 'adstock__Print_pipe__carryover__strength': 0.20342339845001597, 'adstock__Print_pipe__carryover__length': 1, 'adstock__Print_pipe__saturation__a': 0.5047628786530514, 'adstock__Facebook_pipe__carryover__strength': 0.8977201628148074, 'adstock__Facebook_pipe__carryover__length': 1, 'adstock__Facebook_pipe__saturation__a': 0.43439998611263264, 'adstock__Google_pipe__carryover__strength': 0.834188

...

[I 2022-04-12 14:42:32,217] Trial 972 finished with value: 0.6671880472800984 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.1970887644504083, 'adstock__OpenTV_pipe__carryover__length': 6, 'adstock__OpenTV_pipe__saturation__a': 0.9222228592375379, 'adstock__PayTV_pipe__carryover__strength': 0.777688708948149, 'adstock__PayTV_pipe__carryover__length': 5, 'adstock__PayTV_pipe__saturation__a': 0.8754918307290039, 'adstock__Radio_pipe__carryover__strength': 0.9820352832798643, 'adstock__Radio_pipe__carryover__length': 5, 'adstock__Radio_pipe__saturation__a': 0.2703880371029029, 'adstock__Print_pipe__carryover__strength': 0.9710025104847132, 'adstock__Print_pipe__carryover__length': 4, 'adstock__Print_pipe__saturation__a': 0.16058332293708244, 'adstock__Facebook_pipe__carryover__strength': 0.9342362443359642, 'adstock__Facebook_pipe__carryover__length': 0, 'adstock__Facebook_pipe__saturation__a': 0.37391222913854766, 'adstock__Google_pipe__carryover__strength': 0.1002708603

[I 2022-04-12 14:42:35,440] Trial 979 finished with value: 0.5040032617359964 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.1930873522060661, 'adstock__OpenTV_pipe__carryover__length': 6, 'adstock__OpenTV_pipe__saturation__a': 0.9381977137099472, 'adstock__PayTV_pipe__carryover__strength': 0.7645168724482242, 'adstock__PayTV_pipe__carryover__length': 5, 'adstock__PayTV_pipe__saturation__a': 0.9081165927392542, 'adstock__Radio_pipe__carryover__strength': 0.9997652525758299, 'adstock__Radio_pipe__carryover__length': 5, 'adstock__Radio_pipe__saturation__a': 0.254941851114294, 'adstock__Print_pipe__carryover__strength': 0.9814934310493562, 'adstock__Print_pipe__carryover__length': 4, 'adstock__Print_pipe__saturation__a': 0.2293641531633661, 'adstock__Facebook_pipe__carryover__strength': 0.9407440268752197, 'adstock__Facebook_pipe__carryover__length': 0, 'adstock__Facebook_pipe__saturation__a': 0.3760676472847497, 'adstock__Google_pipe__carryover__strength': 0.116677279396

[I 2022-04-12 14:42:38,871] Trial 986 finished with value: 0.6577840349443712 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.25311199250250804, 'adstock__OpenTV_pipe__carryover__length': 6, 'adstock__OpenTV_pipe__saturation__a': 0.9385033823402167, 'adstock__PayTV_pipe__carryover__strength': 0.7853367927577521, 'adstock__PayTV_pipe__carryover__length': 5, 'adstock__PayTV_pipe__saturation__a': 0.8677883314734236, 'adstock__Radio_pipe__carryover__strength': 0.9530946534501552, 'adstock__Radio_pipe__carryover__length': 5, 'adstock__Radio_pipe__saturation__a': 0.2364049446478807, 'adstock__Print_pipe__carryover__strength': 0.9996755293905192, 'adstock__Print_pipe__carryover__length': 4, 'adstock__Print_pipe__saturation__a': 0.16078088712301578, 'adstock__Facebook_pipe__carryover__strength': 0.8992903517749378, 'adstock__Facebook_pipe__carryover__length': 3, 'adstock__Facebook_pipe__saturation__a': 0.38670800447862025, 'adstock__Google_pipe__carryover__strength': 0.11158845

[I 2022-04-12 14:42:42,061] Trial 993 finished with value: 0.6699409581677374 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.22912525100322903, 'adstock__OpenTV_pipe__carryover__length': 6, 'adstock__OpenTV_pipe__saturation__a': 0.9764899292072509, 'adstock__PayTV_pipe__carryover__strength': 0.8088922664954731, 'adstock__PayTV_pipe__carryover__length': 5, 'adstock__PayTV_pipe__saturation__a': 0.8412737682712805, 'adstock__Radio_pipe__carryover__strength': 0.946791090556651, 'adstock__Radio_pipe__carryover__length': 5, 'adstock__Radio_pipe__saturation__a': 0.2661458750785632, 'adstock__Print_pipe__carryover__strength': 0.9810624631753532, 'adstock__Print_pipe__carryover__length': 4, 'adstock__Print_pipe__saturation__a': 0.5571639170039376, 'adstock__Facebook_pipe__carryover__strength': 0.9468850491794732, 'adstock__Facebook_pipe__carryover__length': 0, 'adstock__Facebook_pipe__saturation__a': 0.36459773283976893, 'adstock__Google_pipe__carryover__strength': 0.1296832163

0.6168668414921276

In [151]:
tuned_model.fit(x,y)

[I 2022-04-12 14:42:44,886] A new study created in memory with name: no-name-8fb70c9c-aaf1-46a9-8def-d7ea4626ce96
[I 2022-04-12 14:42:45,129] Trial 0 finished with value: 0.49070085497793625 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.5374425907193954, 'adstock__OpenTV_pipe__carryover__length': 4, 'adstock__OpenTV_pipe__saturation__a': 0.9870184455954389, 'adstock__PayTV_pipe__carryover__strength': 0.2760367691460003, 'adstock__PayTV_pipe__carryover__length': 4, 'adstock__PayTV_pipe__saturation__a': 0.9825239593893744, 'adstock__Radio_pipe__carryover__strength': 0.2624322676509575, 'adstock__Radio_pipe__carryover__length': 4, 'adstock__Radio_pipe__saturation__a': 0.8616785910698014, 'adstock__Print_pipe__carryover__strength': 0.8170383657279878, 'adstock__Print_pipe__carryover__length': 6, 'adstock__Print_pipe__saturation__a': 0.5657519456923042, 'adstock__Facebook_pipe__carryover__strength': 0.1376446394208185, 'adstock__Facebook_pipe__carryover__length': 1, 'adsto

[I 2022-04-12 14:42:46,655] Trial 7 finished with value: 0.43894186688539144 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.2898318765841542, 'adstock__OpenTV_pipe__carryover__length': 0, 'adstock__OpenTV_pipe__saturation__a': 0.15537601453703395, 'adstock__PayTV_pipe__carryover__strength': 0.558174011468129, 'adstock__PayTV_pipe__carryover__length': 1, 'adstock__PayTV_pipe__saturation__a': 0.1831545700788627, 'adstock__Radio_pipe__carryover__strength': 0.38749701017715443, 'adstock__Radio_pipe__carryover__length': 6, 'adstock__Radio_pipe__saturation__a': 0.5365011153157239, 'adstock__Print_pipe__carryover__strength': 0.27767471959696166, 'adstock__Print_pipe__carryover__length': 1, 'adstock__Print_pipe__saturation__a': 0.5753892310430296, 'adstock__Facebook_pipe__carryover__strength': 0.669851838940092, 'adstock__Facebook_pipe__carryover__length': 2, 'adstock__Facebook_pipe__saturation__a': 0.24536017334786253, 'adstock__Google_pipe__carryover__strength': 0.7681414722

[I 2022-04-12 14:42:48,642] Trial 14 finished with value: 0.43607076323917565 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.10013047796562019, 'adstock__OpenTV_pipe__carryover__length': 2, 'adstock__OpenTV_pipe__saturation__a': 0.48055973870236035, 'adstock__PayTV_pipe__carryover__strength': 0.8480426674467205, 'adstock__PayTV_pipe__carryover__length': 0, 'adstock__PayTV_pipe__saturation__a': 0.3039713449785937, 'adstock__Radio_pipe__carryover__strength': 0.9973994797188884, 'adstock__Radio_pipe__carryover__length': 1, 'adstock__Radio_pipe__saturation__a': 0.7472898781069779, 'adstock__Print_pipe__carryover__strength': 0.5671864802839904, 'adstock__Print_pipe__carryover__length': 3, 'adstock__Print_pipe__saturation__a': 0.9564911812142557, 'adstock__Facebook_pipe__carryover__strength': 0.2583875028021227, 'adstock__Facebook_pipe__carryover__length': 2, 'adstock__Facebook_pipe__saturation__a': 0.6355696177568545, 'adstock__Google_pipe__carryover__strength': 0.817260994

[I 2022-04-12 14:42:50,759] Trial 21 finished with value: 0.5485769089160911 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.29571809627505863, 'adstock__OpenTV_pipe__carryover__length': 3, 'adstock__OpenTV_pipe__saturation__a': 0.6528330515776637, 'adstock__PayTV_pipe__carryover__strength': 0.7837570094479992, 'adstock__PayTV_pipe__carryover__length': 2, 'adstock__PayTV_pipe__saturation__a': 0.36685500750020006, 'adstock__Radio_pipe__carryover__strength': 0.8916602518677161, 'adstock__Radio_pipe__carryover__length': 3, 'adstock__Radio_pipe__saturation__a': 0.1932692531809354, 'adstock__Print_pipe__carryover__strength': 0.6876139644937861, 'adstock__Print_pipe__carryover__length': 5, 'adstock__Print_pipe__saturation__a': 0.4354493353441241, 'adstock__Facebook_pipe__carryover__strength': 0.1983680083608922, 'adstock__Facebook_pipe__carryover__length': 1, 'adstock__Facebook_pipe__saturation__a': 0.7303652757543686, 'adstock__Google_pipe__carryover__strength': 0.8179948425

[I 2022-04-12 14:42:53,056] Trial 28 finished with value: 0.56264438611181 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.23920591547290113, 'adstock__OpenTV_pipe__carryover__length': 1, 'adstock__OpenTV_pipe__saturation__a': 0.8742276642810566, 'adstock__PayTV_pipe__carryover__strength': 0.8125784049171889, 'adstock__PayTV_pipe__carryover__length': 5, 'adstock__PayTV_pipe__saturation__a': 0.5036939689759463, 'adstock__Radio_pipe__carryover__strength': 0.6647143220361666, 'adstock__Radio_pipe__carryover__length': 1, 'adstock__Radio_pipe__saturation__a': 0.3958983801433442, 'adstock__Print_pipe__carryover__strength': 0.934079842544901, 'adstock__Print_pipe__carryover__length': 2, 'adstock__Print_pipe__saturation__a': 0.513586984957809, 'adstock__Facebook_pipe__carryover__strength': 0.1889208394078675, 'adstock__Facebook_pipe__carryover__length': 3, 'adstock__Facebook_pipe__saturation__a': 0.35481466844061893, 'adstock__Google_pipe__carryover__strength': 0.93036823842487

...

[I 2022-04-12 14:48:48,646] Trial 973 finished with value: 0.6726220405849954 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.1325069676895064, 'adstock__OpenTV_pipe__carryover__length': 4, 'adstock__OpenTV_pipe__saturation__a': 0.40563157217393975, 'adstock__PayTV_pipe__carryover__strength': 0.6414515061408039, 'adstock__PayTV_pipe__carryover__length': 1, 'adstock__PayTV_pipe__saturation__a': 0.5618696692042439, 'adstock__Radio_pipe__carryover__strength': 0.10090133301603563, 'adstock__Radio_pipe__carryover__length': 0, 'adstock__Radio_pipe__saturation__a': 0.23732043451090673, 'adstock__Print_pipe__carryover__strength': 0.93111974299292, 'adstock__Print_pipe__carryover__length': 3, 'adstock__Print_pipe__saturation__a': 0.9696607402072913, 'adstock__Facebook_pipe__carryover__strength': 0.1557033157105101, 'adstock__Facebook_pipe__carryover__length': 0, 'adstock__Facebook_pipe__saturation__a': 0.11888668141856498, 'adstock__Google_pipe__carryover__strength': 0.961510998

[I 2022-04-12 14:48:51,753] Trial 980 finished with value: 0.6770920634430281 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.1000469441425346, 'adstock__OpenTV_pipe__carryover__length': 4, 'adstock__OpenTV_pipe__saturation__a': 0.41539655339442694, 'adstock__PayTV_pipe__carryover__strength': 0.615922365302547, 'adstock__PayTV_pipe__carryover__length': 1, 'adstock__PayTV_pipe__saturation__a': 0.5910884247672058, 'adstock__Radio_pipe__carryover__strength': 0.16886249518349955, 'adstock__Radio_pipe__carryover__length': 0, 'adstock__Radio_pipe__saturation__a': 0.18375075714023661, 'adstock__Print_pipe__carryover__strength': 0.9862800799238676, 'adstock__Print_pipe__carryover__length': 3, 'adstock__Print_pipe__saturation__a': 0.9814841615152947, 'adstock__Facebook_pipe__carryover__strength': 0.10034012842051421, 'adstock__Facebook_pipe__carryover__length': 0, 'adstock__Facebook_pipe__saturation__a': 0.10387114374241849, 'adstock__Google_pipe__carryover__strength': 0.9640898

[I 2022-04-12 14:48:54,883] Trial 987 finished with value: 0.6745331955321757 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.11763214241069711, 'adstock__OpenTV_pipe__carryover__length': 4, 'adstock__OpenTV_pipe__saturation__a': 0.39475018183518734, 'adstock__PayTV_pipe__carryover__strength': 0.6646307015719158, 'adstock__PayTV_pipe__carryover__length': 1, 'adstock__PayTV_pipe__saturation__a': 0.5753950495963006, 'adstock__Radio_pipe__carryover__strength': 0.10046918540673648, 'adstock__Radio_pipe__carryover__length': 0, 'adstock__Radio_pipe__saturation__a': 0.20293356100469534, 'adstock__Print_pipe__carryover__strength': 0.9837410626830048, 'adstock__Print_pipe__carryover__length': 3, 'adstock__Print_pipe__saturation__a': 0.9996701624523386, 'adstock__Facebook_pipe__carryover__strength': 0.1251191991736697, 'adstock__Facebook_pipe__carryover__length': 0, 'adstock__Facebook_pipe__saturation__a': 0.11798762415350487, 'adstock__Google_pipe__carryover__strength': 0.463526

[I 2022-04-12 14:48:57,985] Trial 994 finished with value: 0.6682741930043278 and parameters: {'adstock__OpenTV_pipe__carryover__strength': 0.17773885443467377, 'adstock__OpenTV_pipe__carryover__length': 4, 'adstock__OpenTV_pipe__saturation__a': 0.4382963146572775, 'adstock__PayTV_pipe__carryover__strength': 0.6259241099581524, 'adstock__PayTV_pipe__carryover__length': 1, 'adstock__PayTV_pipe__saturation__a': 0.6101758454760652, 'adstock__Radio_pipe__carryover__strength': 0.13496561710947677, 'adstock__Radio_pipe__carryover__length': 0, 'adstock__Radio_pipe__saturation__a': 0.1793332210492712, 'adstock__Print_pipe__carryover__strength': 0.9961849918084386, 'adstock__Print_pipe__carryover__length': 3, 'adstock__Print_pipe__saturation__a': 0.9829651595888171, 'adstock__Facebook_pipe__carryover__strength': 0.16065488793700353, 'adstock__Facebook_pipe__carryover__length': 0, 'adstock__Facebook_pipe__saturation__a': 0.12276248983296889, 'adstock__Google_pipe__carryover__strength': 0.9606197

OptunaSearchCV(cv=TimeSeriesSplit(gap=0, max_train_size=None, n_splits=5, test_size=None),
               estimator=Pipeline(steps=[('adstock',
                                          ColumnTransformer(transformers=[('OpenTV_pipe',
                                                                           Pipeline(steps=[('carryover',
                                                                                            ExponentialCarryover()),
                                                                                           ('saturation',
                                                                                            ExponentialSaturation())]),
                                                                           ['OpenTV']),
                                                                          ('PayTV_pipe',
                                                                           Pipeline(steps=[('carryover',
                                                                                            ExponentialCarryover()),
                                                                                           ('satu...
                                    'adstock__Print_pipe__carryover__strength': UniformDistribution(high=1.0, low=0.1),
                                    'adstock__Print_pipe__saturation__a': UniformDistribution(high=1.0, low=0.1),
                                    'adstock__Radio_pipe__carryover__length': IntUniformDistribution(high=6, low=0, step=1),
                                    'adstock__Radio_pipe__carryover__strength': UniformDistribution(high=1.0, low=0.1),
                                    'adstock__Radio_pipe__saturation__a': UniformDistribution(high=1.0, low=0.1)},
               random_state=0)

In [152]:
tuned_model.best_params_

{'adstock__OpenTV_pipe__carryover__strength': 0.10001957737257126,
 'adstock__OpenTV_pipe__carryover__length': 4,
 'adstock__OpenTV_pipe__saturation__a': 0.45394288750202494,
 'adstock__PayTV_pipe__carryover__strength': 0.606994456104799,
 'adstock__PayTV_pipe__carryover__length': 1,
 'adstock__PayTV_pipe__saturation__a': 0.5227856561760266,
 'adstock__Radio_pipe__carryover__strength': 0.1007309499077729,
 'adstock__Radio_pipe__carryover__length': 0,
 'adstock__Radio_pipe__saturation__a': 0.13194280496322494,
 'adstock__Print_pipe__carryover__strength': 0.9795801027455305,
 'adstock__Print_pipe__carryover__length': 3,
 'adstock__Print_pipe__saturation__a': 0.9978542294928142,
 'adstock__Facebook_pipe__carryover__strength': 0.20241547210794847,
 'adstock__Facebook_pipe__carryover__length': 0,
 'adstock__Facebook_pipe__saturation__a': 0.17651869936296513,
 'adstock__Google_pipe__carryover__strength': 0.9334073254021117,
 'adstock__Google_pipe__carryover__length': 0,
 'adstock__Google_pip

In [153]:
pd.set_option('display.max_rows', 30) 

In [154]:
best_params = pd.DataFrame({'params': (tuned_model.best_params_).keys(),
                            'values' : (tuned_model.best_params_).values()})

In [155]:
best_params[['Modelo','Medio','Feature','Parametro']] = best_params.params.str.split('__', expand = True)
best_params['Medio'] = best_params['Medio'].str.replace('_pipe','')
best_params

params  values   Modelo     Medio  \
0     adstock__OpenTV_pipe__carryover__strength   0.100  adstock    OpenTV   
1       adstock__OpenTV_pipe__carryover__length   4.000  adstock    OpenTV   
2           adstock__OpenTV_pipe__saturation__a   0.454  adstock    OpenTV   
3      adstock__PayTV_pipe__carryover__strength   0.607  adstock     PayTV   
4        adstock__PayTV_pipe__carryover__length   1.000  adstock     PayTV   
5            adstock__PayTV_pipe__saturation__a   0.523  adstock     PayTV   
6      adstock__Radio_pipe__carryover__strength   0.101  adstock     Radio   
7        adstock__Radio_pipe__carryover__length   0.000  adstock     Radio   
8            adstock__Radio_pipe__saturation__a   0.132  adstock     Radio   
9      adstock__Print_pipe__carryover__strength   0.980  adstock     Print   
10       adstock__Print_pipe__carryover__length   3.000  adstock     Print   
11           adstock__Print_pipe__saturation__a   0.998  adstock     Print   
12  adstock__Facebook_pipe__carryover__strength   0.202  adstock  Facebook   
13    adstock__Facebook_pipe__carryover__length   0.000  adstock  Facebook   
14        adstock__Facebook_pipe__saturation__a   0.177  adstock  Facebook   
15    adstock__Google_pipe__carryover__strength   0.933  adstock    Google   
16      adstock__Google_pipe__carryover__length   0.000  adstock    Google   
17          adstock__Google_pipe__saturation__a   0.549  adstock    Google   
18     adstock__Email_pipe__carryover__strength   0.778  adstock     Email   
19       adstock__Email_pipe__carryover__length   0.000  adstock     Email   
20           adstock__Email_pipe__saturation__a   0.997  adstock     Email   

       Feature Parametro  
0    carryover  strength  
1    carryover    length  
2   saturation         a  
3    carryover  strength  
4    carryover    length  
5   saturation         a  
6    carryover  strength  
7    carryover    length  
8   saturation         a  
9    carryover  strength  
10   carryover    length  
11  saturation         a  
12   carryover  strength  
13   carryover    length  
14  saturation         a  
15   carryover  strength  
16   carryover    length  
17  saturation         a  
18   carryover  strength  
19   carryover    length  
20  saturation         a

In [156]:
best_params.to_csv('best_params.csv', index = False)

In [157]:
px.bar(best_params.query('Parametro == "length"'),
      x = 'Medio',
      y = 'values',
      color = 'Medio')

In [158]:
0.09400137698181585px.bar(best_params.query('Parametro == "strength"'),
      x = 'Medio',
      y = 'values',
      color = 'Medio')

In [159]:
px.bar(best_params.query('Parametro == "a"'),
      x = 'Medio',
      y = 'values',
      color = 'Medio')

In [160]:
print(tuned_model.best_estimator_.named_steps ['regression']. coef_)

[ 66324.58657163  18992.23921301   5310.67622569  27939.74594359
 -10905.2857295   12447.1318431  105008.63304836]


In [161]:
print(tuned_model.best_estimator_.named_steps ['regression'].intercept_)

121572.4265388315


In [162]:
data_model.columns

Index(['Email', 'Facebook', 'Google', 'OpenTV', 'PayTV', 'Print', 'Radio',
       'Sales'],
      dtype='object')

In [163]:
list(data_model.columns)[:7]

['Email', 'Facebook', 'Google', 'OpenTV', 'PayTV', 'Print', 'Radio']

In [164]:
coefbestparam = pd.DataFrame({'Medio' : list(data_model.columns)[:7],
             'Valores' : tuned_model.best_estimator_.named_steps ['regression']. coef_})
base = {'Medio':'base', 'Valores' : tuned_model.best_estimator_.named_steps ['regression'].intercept_}
coefbestparam = coefbestparam.append(base, ignore_index=True)
coefbestparam.to_csv('coefbestparam.csv', index = False)

/tmp/ipykernel_4761/4131017960.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



In [165]:
data_model[[medio + '_sat' for medio in ['OpenTV', 'PayTV',  
                                         'Print', 'Facebook', 'Google', 
                                         'Radio','Email']]] = tuned_model.best_estimator_.named_steps['adstock'].transform(x)

In [166]:
df2 = data_model[['Sales','OpenTV_sat', 'PayTV_sat', 'Radio_sat', 'Print_sat', 'Facebook_sat', 'Google_sat', 'Email_sat']].corr().round(2)

fig = ff.create_annotated_heatmap( df2.values.tolist(),
                                    x=df2.columns.values.tolist(),
                                    y=df2.index.values.tolist(),
                                    colorscale='Viridis')
fig.update_layout(title_text='Correlacion')
fig['data'][0]['showscale'] = True
fig.show()

In [167]:
for medio in medios:
    rho = best_params.query('Parametro == "a" and Medio == @medio')['values'].values
    data_model[medio +'_Adbug'] = data_model[medio]/(data_model[medio] + (data_model[medio].mean() * rho))

In [168]:
fig = go.Figure()
for i, medio in enumerate(medios):
    medio_sat = medio +'_Adbug'
    data_adstock = data_model
    fig.add_trace(go.Scatter(x=data_adstock[medio], 
                             y=data_adstock[medio_sat],
                            mode='markers',
                            name=medio))
fig.show()

In [169]:
fig = make_subplots(rows=7, cols=1, subplot_titles=medios)
for i, medio in enumerate(medios):
    medio_sat = medio+'_Adbug'
    data_adstock = data_model[data_model[medio_sat] != 0]
    fig.add_trace(go.Scatter(x=data_adstock[medio], y=data_adstock[medio_sat], mode='markers', name=medio), row=i+1, col=1)
fig.update_layout(width=800, height=1500)
fig.show()

In [170]:
data_model.to_csv('DataSaturada.csv')

In [171]:
adstock_data = pd.DataFrame(
    tuned_model.best_estimator_.named_steps['adstock'].transform(x),
    columns=x.columns,
    index=x.index
)
adstock_data.head()

Email  Facebook  Google  OpenTV  PayTV  Print  Radio
Date                                                            
2018-01-07  0.839     0.756   0.000   0.000  0.923  0.780  0.000
2018-01-14  0.342     0.653   0.955   0.389  0.918  0.738  0.659
2018-01-21  0.049     0.000   0.000   0.559  0.000  0.729  0.667
2018-01-28  0.005     0.000   0.000   0.554  0.000  0.000  0.467
2018-02-04  0.001     0.000   0.000   0.622  0.000  0.000  0.364

In [172]:
adstock_data.to_csv('adstock_data.csv')

In [173]:
weights = pd.Series(
    tuned_model.best_estimator_.named_steps['regression'].coef_,
    index=x.columns
)
weights

Email       66324.587
Facebook    18992.239
Google       5310.676
OpenTV      27939.746
PayTV      -10905.286
Print       12447.132
Radio      105008.633
dtype: float64

In [174]:
weights.to_csv('weights.csv')

In [175]:
adstock_data = pd.DataFrame(
    tuned_model.best_estimator_.named_steps['adstock'].transform(x),
    columns=x.columns,
    index=x.index
)
weights = pd.Series(
    tuned_model.best_estimator_.named_steps['regression'].coef_,
    index=x.columns
)

base = tuned_model.best_estimator_.named_steps['regression'].intercept_
unadj_contributions = adstock_data.mul(weights).assign(Base=base)
adj_contributions = (unadj_contributions
                     .div(unadj_contributions.sum(axis=1), axis=0)
                     .mul(y, axis=0)
                    )

In [176]:
adj_contributions.to_csv('adj_contributions.csv')

In [177]:
#adj_contributions = pd.read_csv('./adj_contributions.csv')

In [178]:
adj_contributions.head()

Email  Facebook   Google    OpenTV      PayTV     Print  \
Date                                                                     
2018-01-07 56898.405 14692.079    0.000     0.000 -10296.923  9935.695   
2018-01-14 24929.553 13633.634 5572.585 11936.870 -10998.052 10093.107   
2018-01-21  3589.105     0.000    0.000 17111.234     -0.000  9940.986   
2018-01-28   325.581     0.000    0.000 14694.042     -0.000     0.000   
2018-02-04    38.106     0.000    0.000 19216.552     -0.000     0.000   

               Radio       Base  
Date                             
2018-01-07     0.000 124366.744  
2018-01-14 76111.992 133624.111  
2018-01-21 76667.356 133144.520  
2018-01-28 46532.720 115386.657  
2018-02-04 42293.810 134392.932

In [179]:
adj_contributions = adj_contributions.reset_index()

In [180]:
# ROI
atribucion_ventas_medio = pd.read_csv('./adj_contributions.csv')
atribucion_ventas_medio['Date'] = pd.to_datetime(atribucion_ventas_medio['Date'])
atribucion_ventas_medio = atribucion_ventas_medio.set_index('Date')
atribucion_ventas_medio = atribucion_ventas_medio.rename(columns=lambda x: x+'_revenue')
atribucion_ventas_medio = atribucion_ventas_medio.drop(columns=['Base_revenue'])

investment_medio = pd.read_csv('./Data/MMM.csv')
investment_medio['Date'] = pd.to_datetime(investment_medio['Date'])
investment_medio = investment_medio.set_index('Date')
investment_medio = investment_medio.rename(columns=lambda x: x+'_investment')
investment_medio = investment_medio.drop(columns=['Sales_investment'])

# calcular el ROI para cada medio
atribucion_investment_medio = pd.merge(investment_medio, atribucion_ventas_medio, how='inner', left_index=True, right_index=True)

atribucion_investment_medio = atribucion_investment_medio.reset_index()
atribucion_investment_medio['year_month'] = atribucion_investment_medio['Date'].dt.strftime('%Y-%m')
atribucion_investment_medio = atribucion_investment_medio.groupby(['Date']).sum().reset_index()

amedios3 = ['OpenTV', 'Print', 'Email', 'Radio', 'Facebook', 'Google', 'PayTV']
for medio in amedios3:
    atribucion_investment_medio[medio+'_ROI'] = round((atribucion_investment_medio[medio+'_revenue'] - atribucion_investment_medio[medio+'_investment'])/atribucion_investment_medio[medio+'_investment'],1)


In [181]:
atribucion_investment_medio

Date  OpenTV_investment  PayTV_investment  Radio_investment  \
0   2018-01-07          13637.752         11127.998             0.000   
1   2018-01-14              0.000             0.000          8665.516   
2   2018-01-21              0.000             0.000             0.000   
3   2018-01-28              0.000             0.000             0.000   
4   2018-02-04              0.000             0.000             0.000   
..         ...                ...               ...               ...   
195 2021-10-03              0.000             0.000             0.000   
196 2021-10-10          15872.811             0.000          7939.661   
197 2021-10-17              0.000         13057.231          7878.190   
198 2021-10-24              0.000             0.000             0.000   
199 2021-10-31              0.000             0.000             0.000   

     Print_investment  Facebook_investment  Google_investment  \
0               0.000             3996.636           8049.171   
1            3097.078             3710.392           6375.418   
2            3145.182                0.000           6104.066   
3               0.000                0.000              0.000   
4            2091.329                0.000              0.000   
..                ...                  ...                ...   
195          1422.822                0.000              0.000   
196          2518.880                0.000           8688.287   
197          1905.702             4053.968           6051.444   
198             0.000                0.000              0.000   
199             0.000                0.000              0.000   

     Email_investment  Email_revenue  Facebook_revenue  ...  PayTV_revenue  \
0               0.000      56898.405         14692.079  ...     -10296.923   
1            3532.607      24929.553         13633.634  ...     -10998.052   
2            3648.382       3589.105             0.000  ...          0.000   
3            1597.715        325.581             0.000  ...          0.000   
4            1045.664         38.106             0.000  ...          0.000   
..                ...            ...               ...  ...            ...   
195           850.695       3199.015         12418.986  ...          0.000   
196          5195.986      63116.359             0.000  ...          0.000   
197          2622.643      26478.314         15773.078  ...     -10667.954   
198           994.927       3601.075         12443.359  ...          0.000   
199             0.000        428.788             0.000  ...          0.000   

     Print_revenue  Radio_revenue  OpenTV_ROI  Print_ROI  Email_ROI  \
0         9935.695          0.000      -1.000        inf        inf   
1        10093.107      76111.992         inf      2.300      6.100   
2         9940.986      76667.356         inf      2.200     -0.000   
3            0.000      46532.720         inf        NaN     -0.800   
4            0.000      42293.810         inf     -1.000     -1.000   
..             ...            ...         ...        ...        ...   
195          0.000      32940.097         inf     -1.000      2.800   
196      10946.637      86180.978       0.100      3.300     11.100   
197       9587.151      65564.506         inf      4.000      9.100   
198          0.000      35270.081         inf        NaN      2.600   
199          0.000          0.000         inf        NaN        inf   

     Radio_ROI  Facebook_ROI  Google_ROI  PayTV_ROI  
0          NaN         2.700      -1.000     -1.900  
1        7.800         2.700      -0.100       -inf  
2          inf           NaN      -1.000        NaN  
3          inf           NaN         NaN        NaN  
4          inf           NaN         NaN        NaN  
..         ...           ...         ...        ...  
195        inf           inf         NaN        NaN  
196      9.900           NaN      -0.400        NaN  
197      7.300         2.900      -0.100     -1.800  
198        inf        

In [182]:
def plot_roi(medio_select, atribucion_investment_medio):
    atribucion_investment_medio = atribucion_investment_medio[atribucion_investment_medio[medio_select+'_investment'] != 0]
    roi_plot = make_subplots(specs=[[{"secondary_y": True}]])
    # revenue vs investment
    roi_plot.add_trace(go.Scatter(  x=atribucion_investment_medio[medio_select+'_investment'],
                                    y=atribucion_investment_medio[medio_select+'_revenue'],
                                    mode='markers',
                                    name='Investment vs Revenue'),
                        secondary_y=False)
    # revenue vs ROI
    roi_plot.add_trace(go.Scatter(  x=atribucion_investment_medio[medio_select+'_investment'],
                                    y=atribucion_investment_medio[medio_select+'_ROI'],
                                    mode='markers',
                                    name='Investment vs ROI'),
                        secondary_y=True)
    roi_plot.add_annotation(y = atribucion_investment_medio[medio_select+'_revenue'].max(),
                            x = atribucion_investment_medio[medio_select+'_investment'].min(),
                            text = 'ROI = '+str(round(atribucion_investment_medio[medio_select+'_ROI'].max(),2))+'%' + '<br>' + 'Investment = $'+str(round(atribucion_investment_medio[medio_select+'_investment'].min(),2)),
                            showarrow = True,
                            arrowhead = 1,
                            ax = -75,
                            ay = 0)
    roi_plot.add_annotation(y = atribucion_investment_medio[medio_select+'_revenue'].min(),
                            x = atribucion_investment_medio[medio_select+'_investment'].max(),
                            text = 'ROI = '+str(round(atribucion_investment_medio[medio_select+'_ROI'].min(),2))+'%' + '<br>' + 'Investment = $'+str(round(atribucion_investment_medio[medio_select+'_investment'].max(),2)),
                            showarrow = True,
                            arrowhead = 1,
                            ax = 75,
                            ay = 0)
    roi_plot.add_annotation(y = atribucion_investment_medio[medio_select+'_revenue'].min(),
                            x = atribucion_investment_medio[medio_select+'_investment'].min(),
                            text = 'ROI = '+str(round(atribucion_investment_medio[medio_select+'_ROI'].max(),2))+'%' + '<br>' + 'Revenue = $'+str(round(atribucion_investment_medio[medio_select+'_revenue'].min(),2)),
                            showarrow = True,
                            arrowhead = 1,
                            ax = -75,
                            ay = 0)
    roi_plot.add_annotation(y = atribucion_investment_medio[medio_select+'_revenue'].max(),
                            x = atribucion_investment_medio[medio_select+'_investment'].max(),
                            text = 'ROI = '+str(round(atribucion_investment_medio[medio_select+'_ROI'].min(),2))+'%' + '<br>' + 'Revenue = $'+str(round(atribucion_investment_medio[medio_select+'_revenue'].max(),2)) ,
                            showarrow = True,
                            arrowhead = 1,
                            ax = 75,
                            ay = 0)
    roi_plot.add_annotation(y = atribucion_investment_medio[medio_select+'_revenue'].mean(),
                            x = atribucion_investment_medio[medio_select+'_investment'].mean(),
                            text = 'ROI = '+str(round(atribucion_investment_medio[medio_select+'_ROI'].mean(),2))+'%' + '<br>' + 'Revenue = $'+str(round(atribucion_investment_medio[medio_select+'_revenue'].mean(),2)) + '<br>' + 'Investment = $'+str(round(atribucion_investment_medio[medio_select+'_investment'].mean(),2)),
                            showarrow = True,
                            arrowhead = 1,
                            ax = 150,
                            ay = 0)
    roi_plot.update_layout( legend = dict(
                                        orientation="h",
                                        yanchor="bottom",
                                        y = 1,
                                        xanchor="right",
                                        x = 0.75
                                        )
                            )
    roi_plot.update_layout( yaxis_title='Revenue',
                            yaxis2_title='ROI',
                            xaxis_title='Investment')
    roi_plot.show()

In [183]:

amedios4 = ['Print', 'OpenTV', 'Facebook', 'Google', 'PayTV', 'Email', 'Radio']

plot_roi('Print',atribucion_investment_medio)